In [1]:
import tensorflow as tf
from tensorflow import keras
from keras.models import load_model
import numpy as np
import pyaudio
import time
import librosa
import wave
import queue
import IPython.display as ipd
from IPython.display import Audio
import soundfile as sf
import os
import threading
os.environ["KMP_DUPLICATE_LIB_OK"]="TRUE"

In [2]:
def get_file_path(folder,file_name):
    # Lấy đường dẫn đến thư mục làm việc hiện tại trong Jupyter
    current_directory = os.getcwd()

    # Đường dẫn đến thư mục chứa tệp mô hình "H5"
    h5_folder_path = os.path.join(current_directory, folder)

    # Đường dẫn đến tệp mô hình được chỉ định
    file_path = os.path.join(h5_folder_path, file_name)

    return file_path

In [3]:
# def features_extractor(file_name):
#     audio,sample_rate  = librosa.load(file_name, sr=16000, mono=True)
#     mfcc = librosa.feature.mfcc(y=audio, sr=sample_rate, n_mfcc=40) ## Apllying mfcc
#     mfcc_processed = np.mean(mfcc.T, axis=0) ## some pre-processing
#     return mfcc_processed

In [4]:
# Hàm trích xuất đặc trưng MFCC
def features_extractor(file_name):
    audio, sample_rate = librosa.load(file_name,sr=16000, mono=True)
    frame_length = int(0.025 * sample_rate)
    hop_length = int(0.015 * sample_rate)
    n_fft = 2 ** int(np.ceil(np.log2(frame_length)))
    mfcc = librosa.feature.mfcc(y=audio, sr=sample_rate, n_fft=n_fft, hop_length=hop_length, n_mfcc=13)
    desired_size = 66
    mfccs = np.zeros((13,desired_size))
    mfccs[:, :min(desired_size, mfcc.shape[1])] = mfcc[:, :min(desired_size, mfcc.shape[1])]
    delta_mfccs = librosa.feature.delta(mfccs)
    delta2_mfccs = librosa.feature.delta(mfccs, order=2)
    mfccs_features = np.concatenate((mfccs, delta_mfccs, delta2_mfccs))
    mfccs_features = np.transpose(mfccs_features)

    return mfccs_features

In [5]:
# Hàm dự đoán số 
def mic_check(file_name):
    mfccs_features = features_extractor(file_name)
    # data = np.stack(mfccs_features)
    # data = np.reshape(data,(1,150,39))
    pre_test = best_model.predict(data, verbose=0)
    

In [6]:
# Định nghĩa các hằng số
RATE = 16000
CHUNK = 1024
FORMAT = pyaudio.paInt16
CHANNELS = 1
n_times = int(RATE / CHUNK * 1)  # Number of iterations to record 1 second
# TIME = True
# Khởi tạo Queue
output_folder = 'Wakeup'
os.makedirs(output_folder, exist_ok=True)
p = pyaudio.PyAudio()

In [7]:
# Hàm của luồng 1
def record_audio_1s(file_number, stream):
    global TIME
    print(f"Recording audio for file {file_number}...")
    frames = []

    for _ in range(n_times):
        # Lấy một khung dữ liệu
        data = stream.read(CHUNK)
        frames.append(data)

    # Lưu file âm thanh vào file wav
    filename =  "speech_{}".format(file_number)+".wav"
    with wave.open(filename, 'wb') as wf:
        wf.setnchannels(CHANNELS)
        wf.setsampwidth(p.get_sample_size(FORMAT))
        wf.setframerate(RATE)
        wf.writeframes(b''.join(frames))
    return filename
        

In [8]:
# Hàm của luồng 1
def record_audio():
    print("Recording audio...")
    #Khởi tạo Audio
    stream = p.open(format=FORMAT,
                    channels=1,
                    rate=RATE,
                    input=True,
                    frames_per_buffer=CHUNK)
    for i in range(1000):
        filename = record_audio_1s(i, stream)
        mfcc_processed = features_extractor(filename)
        data = np.stack(mfcc_processed)
        data = np.reshape(data,(66,39,1))
        prediction = best_model.predict(np.expand_dims(data, axis=0))
        print(prediction)
        # if prediction[:, 0] > 0.5:
        if prediction[:, 0] > prediction[:, 1]:
            print(f"Wake Word Detected for ({i})")
            display(Audio(get_file_path('Response','Hello.wav'), rate=16000, autoplay=True))
            time.sleep(1)
            print("Confidence:", prediction[:, 0])
            # display(Audio(filename))
        display(Audio(filename))
        !del {filename}


    

In [9]:
# best_model = load_model("LSTM_model_best.h5", compile=False)
# best_model = load_model("CNN_Class_Wakeup_word.h5", compile=False)
best_model = load_model(get_file_path("WuW_H5","Train_66_WuW_True_AIS_1s.h5"), compile=False)

In [10]:
record_audio()

Recording audio...
Recording audio for file 0...
1/1 [==============================] - 0s 360ms/step
[[1.5396395e-09 1.0000000e+00]]


Recording audio for file 1...
1/1 [==============================] - 0s 34ms/step
[[1.799691e-06 9.999982e-01]]


Recording audio for file 2...
1/1 [==============================] - 0s 26ms/step
[[1.5469057e-07 9.9999982e-01]]


Recording audio for file 3...
1/1 [==============================] - 0s 32ms/step
[[2.9087263e-10 1.0000000e+00]]


Recording audio for file 4...
1/1 [==============================] - 0s 31ms/step
[[4.1133357e-11 1.0000000e+00]]


...

Recording audio for file 235...
1/1 [==============================] - 0s 32ms/step
[[1.9049185e-16 1.0000000e+00]]


Recording audio for file 236...
1/1 [==============================] - 0s 31ms/step
[[1.6192661e-20 1.0000000e+00]]


Recording audio for file 237...
1/1 [==============================] - 0s 31ms/step
[[1.4467332e-12 1.0000000e+00]]


Recording audio for file 238...


KeyboardInterrupt: 